In [1]:
# This Python 3 environment comes with many helpful analytics libraries installed
# It is defined by the kaggle/python Docker image: https://github.com/kaggle/docker-python
# For example, here's several helpful packages to load

import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)

# Input data files are available in the read-only "../input/" directory
# For example, running this (by clicking run or pressing Shift+Enter) will list all files under the input directory

import os
for dirname, _, filenames in os.walk('/kaggle/input'):
    for filename in filenames:
        print(os.path.join(dirname, filename))

# You can write up to 20GB to the current directory (/kaggle/working/) that gets preserved as output when you create a version using "Save & Run All" 
# You can also write temporary files to /kaggle/temp/, but they won't be saved outside of the current session

/kaggle/input/feature-extraction/__results__.html
/kaggle/input/feature-extraction/processed_train.csv
/kaggle/input/feature-extraction/__notebook__.ipynb
/kaggle/input/feature-extraction/__output__.json
/kaggle/input/feature-extraction/processed_test.csv
/kaggle/input/feature-extraction/custom.css
/kaggle/input/test-notebook1/__results__.html
/kaggle/input/test-notebook1/__notebook__.ipynb
/kaggle/input/test-notebook1/__output__.json
/kaggle/input/test-notebook1/custom.css
/kaggle/input/test-notebook1/product_images/91lA6xEQa3L.jpg
/kaggle/input/test-notebook1/product_images/71F7IDJkmRL.jpg
/kaggle/input/test-notebook1/product_images/714T5J3y1oL.jpg
/kaggle/input/test-notebook1/product_images/61ZRFyglLgL.jpg
/kaggle/input/test-notebook1/product_images/81mNIHik0sL.jpg
/kaggle/input/test-notebook1/product_images/61SZDw9k8jL.jpg
/kaggle/input/test-notebook1/product_images/71DD-jmM1FL.jpg
/kaggle/input/test-notebook1/product_images/61z1joYogUL.jpg
/kaggle/input/test-notebook1/product_imag

In [2]:
import torch
from torchvision import transforms
from PIL import Image
from tqdm import tqdm
import timm
from pathlib import Path
import urllib.parse
from sklearn.preprocessing import normalize
CONFIG = {
    "image_model_name": "efficientnet_b0",
    "image_size": 224,
    "batch_size": 64,
    "device": "cuda" if torch.cuda.is_available() else "cpu",
    "knn_neighbors": 10,
}

/usr/local/lib/python3.11/dist-packages/pydantic/_internal/_generate_schema.py:2225: UnsupportedFieldAttributeWarning: The 'repr' attribute with value False was provided to the `Field()` function, which has no effect in the context it was used. 'repr' is field-specific metadata, and can only be attached to a model field using `Annotated` metadata or by assignment. This may have happened because an `Annotated` type alias using the `type` statement was used, or if the `Field()` function was attached to a single member of a union type.
  warnings.warn(
/usr/local/lib/python3.11/dist-packages/pydantic/_internal/_generate_schema.py:2225: UnsupportedFieldAttributeWarning: The 'frozen' attribute with value True was provided to the `Field()` function, which has no effect in the context it was used. 'frozen' is field-specific metadata, and can only be attached to a model field using `Annotated` metadata or by assignment. This may have happened because an `Annotated` type alias using the `type` 

In [3]:
image_model = timm.create_model(CONFIG["image_model_name"], pretrained=True, num_classes=0).to(CONFIG["device"])

model.safetensors:   0%|          | 0.00/21.4M [00:00<?, ?B/s]

In [4]:
def generate_image_embeddings(df, image_folder, model):
    
    model.eval()
    
    transform = transforms.Compose([
        transforms.Resize((CONFIG["image_size"], CONFIG["image_size"])),
        transforms.ToTensor(),
        transforms.Normalize(mean=[0.485, 0.456, 0.406], std=[0.229, 0.224, 0.225]),
    ])
    
    df['image_filename'] = df['image_link'].apply(get_filename_from_url)
    all_embeddings = []
    
    for i in tqdm(range(0, len(df), CONFIG["batch_size"]), desc="Generating Image Embeddings"):
        batch_df = df.iloc[i:i+CONFIG["batch_size"]]
        batch_images = []
        
        for filename in batch_df['image_filename']:
            real_filename = f"product_images/{str(filename)}"
            image_path = os.path.join(image_folder, real_filename)
            try:
                image = Image.open(image_path).convert("RGB")
                image = transform(image)
                batch_images.append(image)
            except (FileNotFoundError, IOError):
                batch_images.append(torch.zeros((3, CONFIG["image_size"], CONFIG["image_size"])))

        if batch_images:
            batch_tensor = torch.stack(batch_images).to(CONFIG["device"])
            with torch.no_grad():
                embeddings = model.forward_features(batch_tensor)
                embeddings = embeddings.mean(dim=[2, 3]) 
            all_embeddings.append(embeddings.cpu().numpy())

    return np.vstack(all_embeddings)

In [5]:
INPUT_DIR_IMAGES = '/kaggle/input/TEST_NOTEBOOK1'
OUTPUT_DIR = '/kaggle/working/'

In [6]:
test_df = pd.read_csv('/kaggle/input/feature-extraction/processed_test.csv')

In [7]:
def get_filename_from_url(url):
    if not isinstance(url, str):
        return None
    try:
        return Path(urllib.parse.unquote(Path(url).name)).name
    except Exception:
        return url.split('/')[-1]

In [8]:
from torchvision import transforms
IMAGE_EMBEDDINGS_TEST_PATH1 = os.path.join(OUTPUT_DIR, 'image_embeddings_test1.npy')
test_image_embeddings = generate_image_embeddings(test_df, INPUT_DIR_IMAGES, image_model)
np.save(IMAGE_EMBEDDINGS_TEST_PATH1, test_image_embeddings)

Generating Image Embeddings: 100%|██████████| 1172/1172 [01:55<00:00, 10.13it/s]
